# Intro

The goal of this project is to build a model that takes in tropical cyclone tracking data and classifies accurately whether readings indicate that a storm is a severe Tropical Storm or a less disruptive disturbance. 

## Business Case

The resulting model will be used by meterologists to understand whether an incoming storm is a major threat to a certain area, and therefore inform news agenices, local governments, and the public to prepare accordingly. 

## Data Understanding

The data for this project is from the National Oceanic and Atmospheric Administration's International Best Track Archive for Climate Stewardship (IBTrACS) project. The goal of this project is make available tropical cyclone best track data to aid understanding of the distribution, frequency, and intensity of tropical cyclones worldwide.

Because the idea is to have a global data source, this data is pulled from many source agenices worldwide, and therefore has many columns that are duplicative, inconsistent, or difficult to interpret. When doing this analysis, reference was made to the data documentation saved in this repository.

[Source](https://www.ncdc.noaa.gov/ibtracs/index.php)

I'll start by importing my data (and all my other imports) to describe it further.

In [1]:
import pandas as pd
import numpy as np
from sklearn.impute import SimpleImputer
from sklearn.model_selection import train_test_split, GridSearchCV
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import roc_curve, auc, accuracy_score, confusion_matrix, classification_report
from sklearn.pipeline import Pipeline
from sklearn.preprocessing import StandardScaler, OneHotEncoder
from sklearn.compose import ColumnTransformer
from sklearn.tree import DecisionTreeClassifier 
import matplotlib.pyplot as plt
import seaborn as sns
sns.set_style('darkgrid')

import warnings
warnings.filterwarnings('ignore')

In [58]:
df = pd.read_csv('data/ibtracs.since1980.list.v04r00.csv', dtype='object', parse_dates=True, skiprows=[1], na_values=' ')
#drop first row as it's a multi index

pd.set_option('display.max_columns', None)
df.head(3)

SID SEASON NUMBER BASIN SUBBASIN  NAME             ISO_TIME  \
0  1980001S13173   1980      1    SP       MM  PENI  1980-01-01 00:00:00   
1  1980001S13173   1980      1    SP       MM  PENI  1980-01-01 03:00:00   
2  1980001S13173   1980      1    SP       MM  PENI  1980-01-01 06:00:00   

  NATURE       LAT      LON WMO_WIND WMO_PRES WMO_AGENCY TRACK_TYPE DIST2LAND  \
0     TS  -12.5000  172.500      NaN      NaN        NaN       main       647   
1     TS  -12.1927  172.441      NaN      NaN        NaN       main       653   
2     TS  -11.9144  172.412      NaN      NaN        NaN       main       670   

  LANDFALL           IFLAG USA_AGENCY USA_ATCF_ID   USA_LAT  USA_LON  \
0      647  O________OO_O_    jtwc_sh    SH051980  -12.5000  172.500   
1      653  P________PP_P_        NaN    SH051980  -12.1825  172.432   
2      670  O________OP_O_    jtwc_sh    SH051980  -11.9000  172.400   

  USA_RECORD USA_STATUS USA_WIND USA_PRES USA_SSHS USA_R34_NE USA_R34_SE  \
0        NaN        NaN       25      NaN       -1        NaN        NaN   
1        NaN        NaN       25      NaN       -1        NaN        NaN   
2        NaN        NaN       25      NaN       -1        NaN        NaN   

  USA_R34_SW USA_R34_NW USA_R50_NE USA_R50_SE USA_R50_SW USA_R50_NW  \
0        NaN        NaN        NaN        NaN        NaN        NaN   
1        NaN        NaN        NaN        NaN        NaN        NaN   
2        NaN        NaN        NaN        NaN        NaN        NaN   

  USA_R64_NE USA_R64_SE USA_R64_SW USA_R64_NW USA_POCI USA_ROCI USA_RMW  \
0        NaN        NaN        NaN        NaN      NaN      NaN     NaN   
1        NaN        NaN        NaN        NaN      NaN      NaN     NaN   
2        NaN        NaN        NaN        NaN      NaN      NaN     NaN   

  USA_EYE TOKYO_LAT TOKYO_LON TOKYO_GRADE TOKYO_WIND TOKYO_PRES TOKYO_R50_DIR  \
0     NaN       NaN       NaN         NaN        NaN        NaN           NaN   
1     NaN       NaN       NaN         NaN        NaN        NaN           NaN   
2     NaN       NaN       NaN         NaN        NaN        NaN           NaN   

  TOKYO_R50_LONG TOKYO_R50_SHORT TOKYO_R30_DIR TOKYO_R30_LONG TOKYO_R30_SHORT  \
0            NaN             NaN           NaN            NaN             NaN   
1            NaN             NaN           NaN            NaN             NaN   
2            NaN             NaN           NaN            NaN             NaN   

  TOKYO_LAND CMA_LAT CMA_LON CMA_CAT CMA_WIND CMA_PRES HKO_LAT HKO_LON  \
0        NaN     NaN     NaN     NaN      NaN      NaN     NaN     NaN   
1        NaN     NaN     NaN     NaN      NaN      NaN     NaN     NaN   
2        NaN     NaN     NaN     NaN      NaN      NaN     NaN     NaN   

  HKO_CAT HKO_WIND HKO_PRES NEWDELHI_LAT NEWDELHI_LON NEWDELHI_GRADE  \
0     NaN      NaN      NaN          NaN          NaN            NaN   
1     NaN      NaN      NaN          NaN          NaN            NaN   
2     NaN      NaN      NaN          NaN          NaN            NaN   

  NEWDELHI_WIND NEWDELHI_PRES NEWDELHI_CI NEWDELHI_DP NEWDELHI_POCI  \
0           NaN           NaN         NaN         NaN           NaN   
1           NaN           NaN         NaN         NaN           NaN   
2           NaN           NaN         NaN         NaN           NaN   

  REUNION_LAT REUNION_LON REUNION_TYPE REUNION_WIND REUNION_PRES REUNION_TNUM  \
0         NaN         NaN          NaN          NaN          NaN          NaN   
1         NaN         NaN          NaN          NaN          NaN          NaN   
2         NaN         NaN          NaN          NaN          NaN          NaN   

  REUNION_CI REUNION_RMW REUNION_R34_NE REUNION_R34_SE REUNION_R34_SW  \
0        NaN         NaN            NaN            NaN            NaN   
1        NaN         NaN            NaN            NaN            NaN   
2        NaN         NaN            NaN            NaN            NaN   

  REUNION_R34_NW REUNION_R50_NE REUNION_R50_SE REUNION_R50_SW RE

In [3]:
print(df.shape)

(271883, 163)


The size of the file is really large but it will get smaller throughout the cleaning process. To start off with, there are 163 columns and they are all reading in as object datatypes. I'll need to go through and clean these up.

In [59]:
df.columns = [x.lower() for x in df.columns]
df.info(verbose=True)

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 271883 entries, 0 to 271882
Data columns (total 163 columns):
sid                 object
season              object
number              object
basin               object
subbasin            object
name                object
iso_time            object
nature              object
lat                 object
lon                 object
wmo_wind            object
wmo_pres            object
wmo_agency          object
track_type          object
dist2land           object
landfall            object
iflag               object
usa_agency          object
usa_atcf_id         object
usa_lat             object
usa_lon             object
usa_record          object
usa_status          object
usa_wind            object
usa_pres            object
usa_sshs            object
usa_r34_ne          object
usa_r34_se          object
usa_r34_sw          object
usa_r34_nw          object
usa_r50_ne          object
usa_r50_se          object
usa_r50_sw          obje

The dataset has readings for storms at multiple points in their progression. There are 4,458 unique storms tracked.

In [6]:
df['sid'].nunique()

4458

My classification task will be to identify whether they are minor storms or severe Tropical Storms. Looking at my target column, 'nature', I can see six different classes that I want to sort into two so this will be a binary - severe storm or not severe. 

NR, not reported, and MX, mixture will be removed as they don't tell me anything. TS, tropical storm, will be my '1' - a severe storm. ET, DS, and SS are extratropical, disturbance, and subtropical - less severe storms. These will be my '0' class. 

In [7]:
df['nature'].unique()

array(['TS', 'NR', 'ET', 'MX', 'SS', 'DS'], dtype=object)

## Data Exploration & Cleaning

The first thing I'm going to do is engineer my Y by making a binary column.

In [13]:
#removing unclassified rows
df.drop(df.loc[df['nature'] == 'NR'].index, inplace=True)
df.drop(df.loc[df['nature'] == 'MX'].index, inplace=True)

#new column  
df['target'] = 0

# loop through the data and input a 1 where the storm is a Tropical storm
for row in df.index:
    if df['nature'][row] == 'TS':
        df['target'][row] = 1

In [14]:
df['target'].value_counts(normalize=True)

1    0.897215
0    0.102785
Name: target, dtype: float64

So there is a pretty severe class imbalance here. Before I address that, I want to define my features. Taking a preliminary look through the columns in the dataframe and the documentation as a guide, I'm selecting the following as potential features to explore. This is a lot less than 163! A lot of these were blank, repeats, or not useful info.

In [48]:
df['week_of_year'] = df['iso_time'].dt.week

0          1
1          1
2          1
3          1
4          1
5          1
6          1
7          1
8          1
9          1
10         1
11         1
12         1
13         1
14         1
15         1
16         1
17         1
18         1
19         1
20         1
21         1
22         1
23         1
24         1
25         1
26         1
27         1
28         1
29         1
30         1
31         1
32         1
33         1
34         1
35         1
36         1
37         1
38         1
39         1
40         1
45         1
46         1
53         1
54         1
55         1
56         1
57         1
58         1
59         1
60         1
61         1
62         1
63         1
64         1
65         1
66         1
67         1
68         1
69         1
70         1
71         1
72         1
73         1
74         1
75         1
76         1
77         1
78         1
79         1
80         1
81         1
82         1
83         1
84         1
85         1
86         1

In [50]:
initial_feats = ['sid', 'season', 'basin', 'subbasin', 'lat', 'lon', 
                 'wmo_wind', 'dist2land', 'ds824_wind', 'td9636_stage', 'storm_speed', 'storm_dir']
xs_df = df[initial_feats]

xs_df[['lat', 'lon', 'dist2land', 'season', 'wmo_wind', 'ds824_wind', 'td9636_stage', 'storm_speed', 'storm_dir']] = xs_df[['lat', 'lon', 'dist2land', 'season', 'wmo_wind', 'ds824_wind', 'td9636_stage', 'storm_speed', 'storm_dir']].apply(pd.to_numeric)

#taking my datetime object and pulling out the week as a feature
df['iso_time'] = pd.to_datetime(df['iso_time'])
xs_df['week_of_year'] = df['iso_time'].dt.week

In [51]:
xs_df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 226423 entries, 0 to 271072
Data columns (total 13 columns):
sid             226423 non-null object
season          226423 non-null int64
basin           190696 non-null object
subbasin        197687 non-null object
lat             226423 non-null float64
lon             226423 non-null float64
wmo_wind        91501 non-null float64
dist2land       226423 non-null int64
ds824_wind      4139 non-null float64
td9636_stage    40790 non-null float64
storm_speed     226422 non-null float64
storm_dir       226422 non-null float64
week_of_year    226423 non-null int64
dtypes: float64(7), int64(3), object(3)
memory usage: 34.2+ MB


So now I have a clearer picture of what my data looks like. I'm going to drop the wind column with only 4K values, and inspect the other columns with nulls more closely. For now I am just focusing on the numerics.

In [57]:
xs_df = xs_df.drop('ds824_wind', axis=1)
y_df = df['target'].to_frame()
clean_df = pd.concat([xs_df, y_df], axis=1)

KeyError: "['ds824_wind'] not found in axis"

In [53]:
clean_df.head()

sid  season basin subbasin      lat      lon  wmo_wind  \
0  1980001S13173    1980    SP       MM -12.5000  172.500       NaN   
1  1980001S13173    1980    SP       MM -12.1927  172.441       NaN   
2  1980001S13173    1980    SP       MM -11.9144  172.412       NaN   
3  1980001S13173    1980    SP       MM -11.6863  172.435       NaN   
4  1980001S13173    1980    SP       MM -11.5000  172.500       NaN   

   dist2land  td9636_stage  storm_speed  storm_dir  week_of_year  target  
0        647           1.0          6.0      351.0             1       1  
1        653           1.0          6.0      351.0             1       1  
2        670           1.0          5.0      358.0             1       1  
3        682           1.0          4.0       12.0             1       1  
4        703           1.0          4.0       22.0             1       1

In [54]:
clean_df['wmo_wind'].isna().sum()/len(clean_df['wmo_wind'])

0.5958846936927785

In [55]:
clean_df['td9636_stage'].isna().sum()/len(clean_df['td9636_stage'])

0.8198504568882137

It appears that the majority of wmo_wind and td9636_stage are also null. I want to look at my data grouped by storm ID to see if there are any other trends I can identify.

In [44]:
pd.set_option('display.max_rows', None)
grouped_df = clean_df.groupby(['sid']).max()
grouped_df

season       lat           lon  wmo_wind  dist2land  \
sid                                                                  
1980001S13173    1980 -11.15250  1.895000e+02      65.0        934   
1980002S15081    1980 -13.88250  8.000000e+01      29.0       2230   
1980003S15137    1980 -14.66000  1.610000e+02      50.0        818   
1980005S11059    1980 -11.00000  5.900000e+01      25.0       1014   
1980005S14120    1980 -13.63330  1.207000e+02     115.0        490   
1980009S14066    1980 -12.00000  6.680000e+01      20.0       1328   
1980010S20043    1980 -16.00000  5.300000e+01      29.0        282   
1980010S22048    1980 -25.30000  5.130000e+01      29.0        410   
1980015S18060    1980 -16.75840  6.800000e+01       NaN       1227   
1980018S10130    1980 -10.10000  1.304000e+02     100.0       2494   
1980021S10090    1980  -9.70000  1.131000e+02      60.0       1356   
1980024S11076    1980 -11.00000  7.600000e+01      29.0       2116   
1980027S11129    1980 -10.50000  1.294000e+02     110.0        611   
1980032S14071    1980 -14.00000  7.100000e+01       NaN       1568   
1980033S12161    1980 -12.20000  1.768000e+02      40.0        491   
1980042S17149    1980 -17.27140  1.603010e+02      55.0        757   
1980043S16131    1980 -15.34750  1.309000e+02     110.0        158   
1980051S12102    1980 -11.60000  1.034240e+02     105.0       2698   
1980052S16155    1980 -16.00000  1.850000e+02      90.0        886   
1980056S15059    1980 -14.59510  6.088830e+01       NaN        958   
1980068S13068    1980 -11.58000  6.750000e+01       NaN       1671   
1980069S12161    1980 -12.00000  1.870000e+02      65.0       1247   
1980073S09133    1980  -8.97751  1.377690e+02      90.0       1502   
1980075S11072    1980 -10.09430  7.150000e+01       NaN       1807   
1980076N06148    1980  13.70100  1.420820e+02       NaN       1101   
1980081S12170    1980 -11.99560  2.060000e+02      55.0       2564   
1980082S19118    1980 -15.99630  1.175000e+02       NaN        735   
1980085S09170    1980  -9.00000  1.940000e+02      55.0        922   
1980085S11135    1980 -11.00000  1.394000e+02       NaN        237   
1980088S14140    1980 -10.49260  1.398000e+02      40.0        237   
1980092S15183    1980 -14.30000  2.010000e+02      35.0       2135   
1980094N02179    1980  21.54290  1.820710e+02      60.0       2659   
1980094N06181    1980   9.00000  1.809000e+02       NaN       2603   
1980126N08150    1980  28.00000  1.441200e+02      85.0       1242   
1980133N07149    1980  50.00000  1.830000e+02     105.0       1708   
1980137N04158    1980  33.00000  1.546500e+02      55.0       1329   
1980140N16116    1980  29.00000  1.210000e+02      55.0        568   
1980161N09249    1980  18.08410 -1.110000e+02     100.0       2199   
1980169N12250    1980  15.70000 -1.099000e+02      50.0       1068   
1980171N06142    1980  23.00000  1.418000e+02      50.0        997   
1980177N13259    1980  22.10000 -1.014000e+02      65.0        809   
1980181N10130    1980  19.12150  1.300000e+02       NaN        426   
1980183N13250    1980  14.46760 -1.104000e+02      45.0       2032   
1980187N09146    1980  38.50000  1.432830e+02      70.0       1532   
1980194N16252    1980  17.20000 -1.077000e+02      40.0        726   
1980197N07154    1980  21.00000  1.492930e+02      85.0       1666   
1980197N15133    1980  22.35070  1.325000e+02       NaN        800   
1980199N31284    1980  30.80000 -7.650000e+01      25.0        390   
1980200N13249    1980  18.50210 -1.110000e+02      45.0       1031   
1980200N25270    1980  30.50000 -9.000000e+01      30.0        435   
1980201N08155    1980  24.46670  1.552000e+02     100.0       1373   
1980204N23287    1980  37.60000 -6.400000e+01      30.0        665   
1980208N23153    1980  58.07470  1.790000e+02      75.0       1857   
1980210N17251    1980  22.70910 -1.090000e+02      65.0       1086   
1980213N11256    1980  25.30000 -1.039000e+02      90.0       1069   
1980214N11330    1980  28

In [41]:
grouped_df['wmo_wind'].isna().sum()/len(grouped_df)

0.1196319018404908

In [42]:
grouped_df['td9636_stage'].isna().sum()/len(grouped_df)

0.8105828220858896

So from looking at the data grouped by storm ID, I can see that the 'stage' feature stopped being recorded altogether in the 90s. This feature isn't going to be useful to me so I'm going to drop it. 11% of the storms have no wind speed recorded, so I could potentially fill that with a mean value. 

In [56]:
clean_df = clean_df.drop(['td9636_stage'], axis=1)
clean_df.head()

sid  season basin subbasin      lat      lon  dist2land  \
0  1980001S13173    1980    SP       MM -12.5000  172.500        647   
1  1980001S13173    1980    SP       MM -12.1927  172.441        653   
2  1980001S13173    1980    SP       MM -11.9144  172.412        670   
3  1980001S13173    1980    SP       MM -11.6863  172.435        682   
4  1980001S13173    1980    SP       MM -11.5000  172.500        703   

   td9636_stage  storm_speed  storm_dir  week_of_year  target  
0           1.0          6.0      351.0             1       1  
1           1.0          6.0      351.0             1       1  
2           1.0          5.0      358.0             1       1  
3           1.0          4.0       12.0             1       1  
4           1.0          4.0       22.0             1       1